# IBM DataScience Professional Certificate
## Applied DataScience Capstone - The Battle of Neighborhoods
_By Kevin Gilson._

---

## Table of contents
* [Introduction](#introduction)
* [Retrieve the dataset](#data)
* [Explore the dataset](#explore)
* [Leverage the Foursquare API](#foursquare)
* [Cluster Neighborhoods](#clusters)
* [Analyze Clusters](#analyze)

## 1. Introduction <a name="introduction"></a>
### 1a. Business problem

Young entrepreneurs are always in demand of good advices, and always looking towards the keys of success.
DataScience can help them analyzing the market, and get information such as:
* Which places of a city are the most prolific?
* Which types of business are present in which areas?
* Which types of business are lacking in which areas?
* ...

This kind of information are particularly relevant for people looking to open food related businesses.

With almost 9 millions people in 2020, London is a big city. Not only is it the capital of the United Kingdom, it is also one of the top financial places in Europe, and a hugely touristic city.
With that in mind, what could possibly leverage a young entrepreneur looking to start his Food-Truck in London, if he wanted to be successful? What is the most prevalent types of shops? Where are located the _hot_ zone of the city? Which place would be best to maximize his profit?

Thanks to Data Science, we have a way to analyze raw data and come up with suggestions to help this young man, grow as a successful entrepreneur.
And who knows, theses information might as well help him make it big in 10 years.

### 1b. Data

London is split into Borough, holding various Neighborhoods.

In order to leverage further geographical data, we will first scrape Wikipedia to get the complete list of each Borough and Neighborhoods.
Then, we will use Python libraries to link each Neighborhoods to its relative geographical coordinates.
After that, we will leverage the Foursquare location data to retrieve their attributes, cluster zones, and most importantly come up with suggestions on the best places to install a food truck.

Our primary data, scraped from Wikipedia, adopt the form of:

|Location|London Borough|Post Town|Postcode District|Dial code|OS Grid Ref|
|--------|--------------|---------|-----------------|---------|-----------|
|Abbey Wood|Bexley, Greenwich [7]|LONDON|SE2|020|TQ465785|
|Acton|Ealing, Hammersmith and Fulham[8]|LONDON|W3, W4|020|TQ205805|
|Addington|Croydon[8]|CROYDON|CR0|020|TQ375645|
|Addiscombe|Croydon[8]|CROYDON|CR0|020|TQ345665|
|Albany Park|Bexley|BEXLEY, SIDCUP|DA5, DA14|020|TQ478728|

As we can see, the data will need to be cleansed, but it is also important to note that OS Grid References can quite easily be converted into coordinates.

### 1c. Preliminary steps

Before starting our analysis, let's first import the libaries we will need along our computations:

In [1]:
# Regular expression
import re

# Handle data in a vectorized way
import numpy as np

# Data analysis
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

# Clustering
from sklearn.cluster import KMeans

# JSON files
import json

# Handle GET / POST requests
import requests

# Convert an address into coordinates
!pip install geopy
from geopy.geocoders import Nominatim

# Coordinates
!pip install geocoder
import geocoder # Geographical library

# OS Grid References converter
!pip install OSGridConverter
from OSGridConverter import grid2latlong

# Web scraping
!pip install beautifulsoup4
from bs4 import BeautifulSoup # web scraping library

# Parser
!pip install lxml
import lxml # parser library

# URL opening
import urllib.request as req # URL opening library

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# Map rendering
!pip install folium==0.5.0
import folium

# Python ENV file
!pip install python-dotenv
from dotenv import load_dotenv

# Password input
import getpass

# Importation confirmation
print('Libraries installed and imported.')

Libraries installed and imported.


---

## 2. Retrieve the dataset  <a name="introduction"></a>

### 2a. Scrape the WikiPedia page

As the first step, we will need to scrape the WikiPedia page in order to retrieve its table, and therefore datas about the London Districts and Areas.
In order to do so, we will:
1. Scrape the page using BeautifulSoup;
2. Convert the OS Grid References found to coordinates (latitude, longitude) using the OSGRridConverter library; missing OS Grid References will results in NaN values for their coordinates;
3. Check the shape of the recovered dataframe

In [2]:
url_wiki = "https://en.wikipedia.org/wiki/List_of_areas_of_London"

# Scrape the page with BeautifulSoup
page = req.urlopen(url_wiki)
soup = BeautifulSoup(page, "lxml")
all_tables = soup.find_all("table")

# Initiate the dataframe
column_names = ['Location', 'London Borough', 'Post Town',
                'Post District', 'Dial Code', 'OS Grid Ref',
                'Latitude', 'Longitude']
wiki_data = pd.DataFrame(columns=column_names)

# Loop through the scraping and extract the second table (first one is the Contents)
for row in all_tables[1].find_all('tr'):
    cells = row.findAll('td')
    if len(cells)==6:
        #print(cells)
        wiki_location = cells[0].text.strip()
        wiki_borough = cells[1].text.strip()
        wiki_town = cells[2].text.strip()
        wiki_district = cells[3].text.strip()
        wiki_dial = cells[4].text.strip()
        
        wiki_gridref = cells[5].text.strip()
        try:
            wiki_latlong = grid2latlong(wiki_gridref)
        except:
            wiki_latlong.latitude = 'NaN'
            wiki_latlong.longitude = 'NaN'
        
        wiki_data = wiki_data.append({'Location': wiki_location,
                                     'London Borough': wiki_borough,
                                     'Post Town': wiki_town,
                                     'Post District': wiki_district,
                                     'Dial Code': wiki_dial,
                                     'OS Grid Ref': wiki_gridref,
                                     'Latitude': wiki_latlong.latitude,
                                     'Longitude': wiki_latlong.longitude}
                                    , ignore_index=True)

# Check the results
print("The resulting dataframe has a shape of: {}\n".format(wiki_data.shape))
wiki_data.head()

The resulting dataframe has a shape of: (533, 8)



Location                     London Borough       Post Town  \
0   Abbey Wood             Bexley,  Greenwich [7]          LONDON   
1        Acton  Ealing, Hammersmith and Fulham[8]          LONDON   
2    Addington                         Croydon[8]         CROYDON   
3   Addiscombe                         Croydon[8]         CROYDON   
4  Albany Park                             Bexley  BEXLEY, SIDCUP   

  Post District Dial Code OS Grid Ref Latitude  Longitude  
0           SE2       020    TQ465785  51.4865   0.109318  
1        W3, W4       020    TQ205805  51.5106  -0.264585  
2           CR0       020    TQ375645  51.3629 -0.0257799  
3           CR0       020    TQ345665  51.3816 -0.0681255  
4     DA5, DA14       020    TQ478728  51.4349   0.125663

### 2b. Upgrade the data

We can see that the resulting dataframe isn't looking its best; let's upgrade it a bit:
1. First we will drop columns that won't be used later;
2. Then we will rename a few of the remaining ones into clearer names;
3. Finally we will reorder the columns.

In [3]:
# Drop useless columns
wiki_data.drop(columns=['Post District'
                        ,'Dial Code'
                        ,'OS Grid Ref'], axis=1, inplace=True)

# Rename columns
wiki_data.rename(columns={'Location':'Neighborhood'
                          ,'London Borough':'Borough'
                          ,'Post Town':'Town'}, inplace=True)

# Reorder
wiki_data = wiki_data[['Borough'
                       ,'Neighborhood'
                       ,'Town'
                       ,'Latitude'
                       ,'Longitude']]
#
wiki_data.head()

Borough Neighborhood            Town Latitude  \
0             Bexley,  Greenwich [7]   Abbey Wood          LONDON  51.4865   
1  Ealing, Hammersmith and Fulham[8]        Acton          LONDON  51.5106   
2                         Croydon[8]    Addington         CROYDON  51.3629   
3                         Croydon[8]   Addiscombe         CROYDON  51.3816   
4                             Bexley  Albany Park  BEXLEY, SIDCUP  51.4349   

   Longitude  
0   0.109318  
1  -0.264585  
2 -0.0257799  
3 -0.0681255  
4   0.125663

### 2c. Clean the data

We can see a few problems with our data, such as:
* Some values contains WikiPedia links references (i.e. "[1]");
* Some Neighborhoods are affected to two or more Towns;
* Some values are followed by explainations in between paratheses;
* The case of the data are not normalized, mixing upper and lower cases.

Let's define a function that will use regular expression to clean the data of brackets, parentheses, and others.
And then, let's capitalize each value (i.e. "VALUES" and "values" will become "Values"):

In [4]:
# Cleaning function, based on RegEx patterns
def Clean_DataEnd(raw_data, pattern):
    if re.search(pattern, str(raw_data)):
        pos = re.search(pattern, str(raw_data)).start()
        return raw_data[:pos]
    else:
        return raw_data

# Fix wikipedia references, double values, and annotations
for col in wiki_data.select_dtypes(include='object').columns:
    wiki_data[col] = wiki_data[col].apply(Clean_DataEnd, pattern=' \[.*')
    wiki_data[col] = wiki_data[col].apply(Clean_DataEnd, pattern='\[.*')
    wiki_data[col] = wiki_data[col].apply(Clean_DataEnd, pattern=' \(.*')
    wiki_data[col] = wiki_data[col].apply(Clean_DataEnd, pattern=', .*')
    wiki_data[col] = wiki_data[col].apply(Clean_DataEnd, pattern=' and .*')
                       
# Capitalize data - Use title to capitalize each words
for col in ['Borough','Neighborhood','Town']:
    wiki_data[col] = wiki_data[col].str.title()

# Check
wiki_data.head()

Borough Neighborhood     Town Latitude  Longitude
0   Bexley   Abbey Wood   London  51.4865   0.109318
1   Ealing        Acton   London  51.5106  -0.264585
2  Croydon    Addington  Croydon  51.3629 -0.0257799
3  Croydon   Addiscombe  Croydon  51.3816 -0.0681255
4   Bexley  Albany Park   Bexley  51.4349   0.125663

### 2d. Handle missing values

Before going further, we want to make sure that we have the coordinates of each neighborhoods.
Let's check the Latitudes and Longitudes:

In [5]:
print(wiki_data[wiki_data['Latitude'] == 'NaN'])
print(wiki_data[wiki_data['Longitude'] == 'NaN'])

     Borough Neighborhood       Town Latitude Longitude
53    Bexley      Blendon     Bexley      NaN       NaN
233  Bromley    Hazelwood  Orpington      NaN       NaN
     Borough Neighborhood       Town Latitude Longitude
53    Bexley      Blendon     Bexley      NaN       NaN
233  Bromley    Hazelwood  Orpington      NaN       NaN


We can see that two Neighborhoods are missing their coordinates.

Using the GeoCoder library, let's retrieve their latitudes and longitudes:

In [6]:
# Define a function to retrieve the coordinates, using ArcGis instead of Google for better performances
def GetCoordinates(df):
    bor = df['Borough']
    neigh = df['Neighborhood']
    town = df['Town']
    
    lat_lng_coords = None
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, London'.format(neigh))
        lat_lng_coords = g.latlng
    lat = lat_lng_coords[0]
    long = lat_lng_coords[1]
    lst = {'Borough': bor,
           'Neighborhood': neigh,
           'Town': town,
           'Latitude': lat,
           'Longitude': long}
    return pd.Series(lst)

# Apply the function to missing coordinates
wiki_data[wiki_data['Latitude'] == 'NaN'] = wiki_data[wiki_data['Latitude'] == 'NaN'].apply(GetCoordinates, axis=1)

# Check if there is any remaining NaN values
print(wiki_data[wiki_data['Latitude'] == 'NaN'])
print(wiki_data[wiki_data['Longitude'] == 'NaN'])

Empty DataFrame
Columns: [Borough, Neighborhood, Town, Latitude, Longitude]
Index: []
Empty DataFrame
Columns: [Borough, Neighborhood, Town, Latitude, Longitude]
Index: []


Now that we are satisfied with our dataset, let's create a copy on which we will be working on, and keep the *wiki_data* as an untouch orignal data frame:

In [7]:
# Create a copy of the dataframe
neighborhoods = wiki_data.copy()

---

## 3. Explore the dataset  <a name="explore"></a>
Let's have a first look at how our dataset look, by looking at its shape, and list its Neighborhoods and Towns:

In [8]:
print('The dataframe has {} boroughs, {} neighborhoods, and {} towns.'.format(
        len(neighborhoods['Borough'].unique()),
        len(neighborhoods['Town'].unique()),
        neighborhoods.shape[0]
    )
)
print('\nThe boroughs are the following:\n{}'.format(neighborhoods['Borough'].unique()))
print('\nThe towns are the following:\n{}'.format(neighborhoods['Town'].unique()))

The dataframe has 35 boroughs, 64 neighborhoods, and 533 towns.

The boroughs are the following:
['Bexley' 'Ealing' 'Croydon' 'Redbridge' 'City' 'Westminster' 'Brent'
 'Bromley' 'Islington' 'Havering' 'Barnet' 'Enfield' 'Wandsworth'
 'Southwark' 'Barking' 'Richmond Upon Thames' 'Newham' 'Sutton' 'Lewisham'
 'Harrow' 'Camden' 'Kingston Upon Thames' 'Tower Hamlets' 'Greenwich'
 'Haringey' 'Hounslow' 'Lambeth' 'Kensington' 'Waltham Forest' 'Merton'
 'Hillingdon' 'Hackney' 'Dartford' 'Islington & City' 'Hammersmith']

The towns are the following:
['London' 'Croydon' 'Bexley' 'Ilford' 'Wembley' 'Westerham' 'Hornchurch'
 'Barnet' 'Barking' 'Bexleyheath' 'Dartford' 'Beckenham' 'Dagenham'
 'Wallington' 'Harrow' 'Sutton' 'Belvedere' 'Surbiton' 'Bromley' 'Sidcup'
 'Enfield' 'Brentford' 'Edgware' 'Carshalton' 'Romford' 'Sutton/Merton'
 'Orpington' 'Chessington' 'Chislehurst' 'Erith' 'West Wickham'
 'Kingston Upon Thames' 'Coulsdon' 'Uxbridge' 'Hounslow' 'Upminster'
 'Sevenoaks' 'Feltham' 'Welling

Considering that we are analyzing London, it might be appropriate to retrieve its coordinates:

In [9]:
address = 'London'
geolocator = Nominatim(user_agent="london_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of London, UK are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of London, UK are 51.5073219, -0.1276474.


Now let's plot the neighborhoods on a map of London, in order to get a better view of the situation; we will leverage the coordinates that we just found to center the map:

In [10]:
# Create map of London using latitude and longitude values
map_london = folium.Map(location=[latitude, longitude], zoom_start=10)

# Add markers corresponding to the neighborhoods to the map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_london)  

# Display the map
map_london

As we can see, the neighborhoods are pretty spread appart. Therefore, it migth be best to create a sub-set of the data focusing on the Town of London:

In [11]:
# Extract rows with a Borough containing Toronto into a new dataframe
london_data = neighborhoods[neighborhoods['Town'].str.contains("London")].reset_index(drop=True)

# Check results
print(london_data.shape)
print('\n')
london_data.head()

(305, 5)




Borough Neighborhood    Town Latitude  Longitude
0       Bexley   Abbey Wood  London  51.4865   0.109318
1       Ealing        Acton  London  51.5106  -0.264585
2         City      Aldgate  London  51.5149 -0.0783556
3  Westminster      Aldwych  London  51.5128  -0.117388
4      Bromley      Anerley  London  51.4086 -0.0669885

Let's now compare the two dataset on a map, by plotting first every neighborhoods in blue, then turning red the ones in London city:

In [12]:
# Create map of London using latitude and longitude values
map_london_city = folium.Map(location=[latitude, longitude], zoom_start=10)

# Add markers corresponding to the neighborhoods to the map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_london_city)  

# Add markers corresponding to the neighborhoods to the map
for lat, lng, borough, neighborhood in zip(london_data['Latitude'], london_data['Longitude'], london_data['Borough'], london_data['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_london_city)  

# Display the map
map_london_city

We can see that it is already better. We are now ready to skip to the next phase of our analysis.

---

## 4. Leverage the Foursquare API  <a name="foursquare"></a>

Using the Foursquare API, we will retrieve more informations regarding our neighborhoods.
In order to use it, we first need to set-up our credentials.

For confidentiality purposes, we will try to load then from a *.env* file, and if no results are retrieved, we prompt for a secrured input, using the GetPass library:

In [13]:
# Try to load .env file
try:
    load_dotenv()
    CLIENT_ID = os.getenv('CLIENT_ID')
    CLIENT_SECRET = os.getenv('CLIENT_SECRET')
# If no .env file available, ask for user input
except:
    CLIENT_ID = getpass.getpass(prompt="Please type your CLIENT_ID: ")
    CLIENT_SECRET = getpass.getpass(prompt="Please  type your CLIENT_SECRET")

# Other parameters
VERSION = '20180605'
LIMIT = 100
radius = 500

# Print end of credentials
print('Your credentials:')
print('CLIENT_ID: {}{}'.format((len(CLIENT_ID)-4)*"*", CLIENT_ID[-4:]))
print('CLIENT_SECRET: {}{}'.format((len(CLIENT_SECRET)-4)*"*", CLIENT_SECRET[-4:]))

Please type your CLIENT_ID:  ················································
Please  type your CLIENT_SECRET ················································


Your credentials:
CLIENT_ID: ********************************************UXXI
CLIENT_SECRET: ********************************************RJLJ


Now we will define a function to retrieve venues for a fiven neighborhood:

In [14]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    venues_list=[]
    i = 0
    for name, lat, lng in zip(names, latitudes, longitudes):
        i = i + 1
        print('{} - {}'.format(i, name))
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

The Foursquare API is limited to 950 request per day for a free user, therefor, we will store the resulting dataframe into a csv file, in case we need to re-run the whole notebook.

If we reach our limit, or if the API fail, we will read the data from the CSV file.

In [15]:
try:
    london_venues = getNearbyVenues(names=london_data['Neighborhood'],
                                    latitudes=london_data['Latitude'],
                                    longitudes=london_data['Longitude'])
    london_venus.to_csv('london_venues.csv', index = False)
except:
    london_venues = pd.read_csv('london_venues.csv')

1 - Abbey Wood
2 - Acton
3 - Aldgate
4 - Aldwych
5 - Anerley
6 - Angel
7 - Archway
8 - Arnos Grove
9 - Balham
10 - Bankside
11 - Barbican
12 - Barnes
13 - Barnet Gate
14 - Barnsbury
15 - Battersea
16 - Bayswater
17 - Beckton
18 - Bedford Park
19 - Belgravia
20 - Bellingham
21 - Belsize Park
22 - Bermondsey
23 - Bethnal Green
24 - Blackfriars
25 - Blackheath
26 - Blackheath Royal Standard
27 - Blackwall
28 - Bloomsbury
29 - Bounds Green
30 - Bow
31 - Bowes Park
32 - Brent Cross
33 - Brent Park
34 - Brixton
35 - Brockley
36 - Bromley
37 - Brompton
38 - Brondesbury
39 - Brunswick Park
40 - Burroughs
41 - Camberwell
42 - Cambridge Heath
43 - Camden Town
44 - Canary Wharf
45 - Cann Hall
46 - Canning Town
47 - Canonbury
48 - Castelnau
49 - Catford
50 - Chalk Farm
51 - Charing Cross
52 - Charlton
53 - Chelsea
54 - Childs Hill
55 - Chinatown
56 - Chinbrook
57 - Chingford
58 - Chiswick
59 - Church End
60 - Church End
61 - Clapham
62 - Clerkenwell
63 - Colindale
64 - Colliers Wood
65 - Colney Ha

Let's now have a look at the resulting dataframe:

In [16]:
print(london_venues.shape)
print('\n')
london_venues.head()

(9140, 7)




Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0   Abbey Wood              51.486484                0.109318   
1   Abbey Wood              51.486484                0.109318   
2   Abbey Wood              51.486484                0.109318   
3   Abbey Wood              51.486484                0.109318   
4   Abbey Wood              51.486484                0.109318   

                             Venue  Venue Latitude  Venue Longitude  \
0                       Co-op Food       51.487650         0.113490   
1                   Bostal Gardens       51.486670         0.110462   
2  Neem Tree Pharmacy in Abbeywood       51.487543         0.113361   
3   Othalias Security Services U K       51.483521         0.105464   
4                 Red barbars shop       51.484588         0.103603   

   Venue Category  
0   Grocery Store  
1      Playground  
2        Pharmacy  
3     IT Services  
4  Cosmetics Shop

Now that we have all the venues, we shall group them by neighborhoods:

In [17]:
london_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Abbey Wood                                     5                       5   
Acton                                         12                      12   
Aldgate                                      100                     100   
Aldwych                                      100                     100   
Anerley                                        5                       5   
Angel                                         15                      15   
Archway                                       27                      27   
Arnos Grove                                    4                       4   
Balham                                        56                      56   
Bankside                                      36                      36   
Barbican                                      79                      79   
Barnes                                        18                      18   
Barnet Gate                                    2                       2   
Barnsbury                                     28                      28   
Battersea                                     23                      23   
Bayswater                                     67                      67   
Beckton                                        9                       9   
Bedford Park                                  10                      10   
Belgravia                                     73                      73   
Bellingham                                     2                       2   
Belsize Park                                  27                      27   
Bermondsey                                    61                      61   
Bethnal Green                                 59                      59   
Blackfriars                                   49                      49   
Blackheath                                    23                      23   
Blackheath Royal Standard                     13                      13   
Blackwall                                     19                      19   
Bloomsbury                                   100                     100   
Bounds Green                                   9                       9   
Bow                                           39                      39   
Bowes Park                                    18                      18   
Brent Cross                                   27                      27   
Brent Park                                     7                       7   
Brixton                                       85                      85   
Brockley                                      14                      14   
Bromley                                       14                      14   
Brompton                                      73                      73   
Brondesbury                                   28                      28   
Brunswick Park                                 4                       4   
Burroughs                                     13                      13   
Camberwell                                    58                      58   
Cambridge Heath                               49                      49   
Camden Town                                   20                      20   
Canary Wharf                                 100                     100   
Cann Hall                                     37                      37   
Canning Town                                   4                       4   
Canonbury                                     17                      17   
Castelnau                                     12                      12   
Catford                                        4                       4   
Chalk Farm                                    81                      81   
Charing Cross                                100                     100   

Let's also have a look at how many unique venues categories there is:

In [18]:
print('There are {} uniques categories.'.format(len(london_venues['Venue Category'].unique())))

There are 389 uniques categories.


We now have everything we need to move on to the next step, and analyze the neighborhoods.

---

## 5. Analyze each Neighborhoods

The first thing we should do is create a new dataframe using the One-Hot Encoding technique.
This method will create a boolean column for each venue category.

In [19]:
# One hot encoding
london_onehot = pd.get_dummies(london_venues[['Venue Category']], prefix="", prefix_sep="")

# Add neighborhood column back to dataframe
london_onehot['Neighborhood'] = london_venues['Neighborhood'] 

# Move neighborhood column to the first column
fixed_columns = ['Neighborhood']  + [col for col in london_onehot if col != 'Neighborhood']
london_onehot = london_onehot[fixed_columns]

# Check results
print(london_onehot.shape)
print('\n')
london_onehot.head()

(9140, 389)




Neighborhood  Acai House  Accessories Store  Afghan Restaurant  \
0   Abbey Wood           0                  0                  0   
1   Abbey Wood           0                  0                  0   
2   Abbey Wood           0                  0                  0   
3   Abbey Wood           0                  0                  0   
4   Abbey Wood           0                  0                  0   

   African Restaurant  American Restaurant  Antique Shop  Aquarium  Arcade  \
0                   0                    0             0         0       0   
1                   0                    0             0         0       0   
2                   0                    0             0         0       0   
3                   0                    0             0         0       0   
4                   0                    0             0         0       0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0                 0                       0            0           0   
1                 0                       0            0           0   
2                 0                       0            0           0   
3                 0                       0            0           0   
4                 0                       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0                    0                 0                   0   
1                    0                 0                   0   
2                    0                 0                   0   
3                    0                 0                   0   
4                    0                 0                   0   

   Australian Restaurant  Austrian Restaurant  Auto Garage  Auto Workshop  \
0                      0                    0            0              0   
1                      0                    0            0              0   
2                      0                    0            0              0   
3                      0                    0            0              0   
4                      0                    0            0              0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery  Bar  Baseball Field  \
0          0           0           0       0    0               0   
1          0           0           0       0    0               0   
2          0           0           0       0    0               0   
3          0           0           0       0    0               0   
4          0           0           0       0    0               0   

   Basketball Court  Beach  Bed & Breakfast  Beer Bar  Beer Garden  \
0                 0      0                0         0            0   
1                 0      0                0         0            0   
2                 0      0                0         0            0   
3                 0      0                0         0            0   
4                 0      0                0         0            0   

   Beer Store  Betting Shop  Bike Rental / Bike Share  Bike Shop  Bistro  \
0           0             0                         0          0       0   
1           0             0                         0          0       0   
2           0             0                         0          0       0   
3           0             0                         0          0       0   
4           0             0                         0          0       0   

   Boarding House  Boat or Ferry  Bookstore  Botanical Garden  Boutique  \
0               0              0          0                 0         0   
1               0              0          0                 0         0   
2               0              0          0                 0         0   
3               0              0          0                 0         0   
4               0              0          0                 0         0   

   Bowling Alley  Bowling Green  Brasserie  Brazilian Restaurant  \
0              0              0

Now that we have created the dummies columns, let's group the data by neighborhoods:

In [20]:
london_grouped = london_onehot.groupby('Neighborhood').mean().reset_index()

# Check results
print(london_grouped.shape)
print('\n')
london_grouped

(301, 389)




Neighborhood  Acai House  Accessories Store  \
0                   Abbey Wood        0.00           0.000000   
1                        Acton        0.00           0.000000   
2                      Aldgate        0.00           0.000000   
3                      Aldwych        0.00           0.000000   
4                      Anerley        0.00           0.000000   
5                        Angel        0.00           0.000000   
6                      Archway        0.00           0.000000   
7                  Arnos Grove        0.00           0.000000   
8                       Balham        0.00           0.000000   
9                     Bankside        0.00           0.000000   
10                    Barbican        0.00           0.000000   
11                      Barnes        0.00           0.000000   
12                 Barnet Gate        0.00           0.000000   
13                   Barnsbury        0.00           0.000000   
14                   Battersea        0.00           0.000000   
15                   Bayswater        0.00           0.000000   
16                     Beckton        0.00           0.000000   
17                Bedford Park        0.00           0.000000   
18                   Belgravia        0.00           0.000000   
19                  Bellingham        0.00           0.000000   
20                Belsize Park        0.00           0.000000   
21                  Bermondsey        0.00           0.000000   
22               Bethnal Green        0.00           0.000000   
23                 Blackfriars        0.00           0.000000   
24                  Blackheath        0.00           0.000000   
25   Blackheath Royal Standard        0.00           0.000000   
26                   Blackwall        0.00           0.000000   
27                  Bloomsbury        0.00           0.000000   
28                Bounds Green        0.00           0.000000   
29                         Bow        0.00           0.000000   
30                  Bowes Park        0.00           0.000000   
31                 Brent Cross        0.00           0.000000   
32                  Brent Park        0.00           0.000000   
33                     Brixton        0.00           0.000000   
34                    Brockley        0.00           0.000000   
35                     Bromley        0.00           0.000000   
36                    Brompton        0.00           0.000000   
37                 Brondesbury        0.00           0.000000   
38              Brunswick Park        0.00           0.000000   
39                   Burroughs        0.00           0.000000   
40                  Camberwell        0.00           0.000000   
41             Cambridge Heath        0.00           0.000000   
42                 Camden Town        0.00           0.000000   
43                Canary Wharf        0.00           0.000000   
44                   Cann Hall        0.00           0.000000   
45                Canning Town        0.00           0.000000   
46                   Canonbury        0.00           0.000000   
47                   Castelnau        0.00           0.000000   
48                     Catford        0.00           0.000000   
49                  Chalk Farm        0.00           0.000000   
50               Charing Cross        0.00           0.000000   
51                    Charlton        0.00           0.000000   
52                     Chelsea        0.00           0.000000   
53                 Childs Hill        0.00           0.000000   
54                   Chinatown        0.00           0.000000   
55                   Chinbrook        0.00           0.000000   
56                   Chingford        0.00           0.000000   
57                    Chiswick        0.00           0.000000   
58                  Church End        0.00           0.000000   
59                     Clapham        0.00           0.000000   
60                 Clerkenwell        0.00           

In its current form, the dataset is pretty much unreadable. So let's have a look at the Top 5 venues per neighborhoods:

In [21]:
num_top_venues = 5

for hood in london_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = london_grouped[london_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Abbey Wood----
            venue  freq
0      Playground   0.2
1  Cosmetics Shop   0.2
2   Grocery Store   0.2
3     IT Services   0.2
4        Pharmacy   0.2


----Acton----
                  venue  freq
0  Gym / Fitness Center  0.17
1                   Pub  0.17
2             Mini Golf  0.08
3              Creperie  0.08
4                  Park  0.08


----Aldgate----
                  venue  freq
0           Coffee Shop  0.08
1                 Hotel  0.07
2          Cocktail Bar  0.05
3  Gym / Fitness Center  0.04
4            Restaurant  0.04


----Aldwych----
          venue  freq
0       Theater  0.09
1         Hotel  0.06
2   Coffee Shop  0.06
3           Pub  0.05
4  Burger Joint  0.05


----Anerley----
            venue  freq
0   Grocery Store   0.4
1   Train Station   0.2
2  Hardware Store   0.2
3            Park   0.2
4      Acai House   0.0


----Angel----
                  venue  freq
0         Grocery Store  0.20
1                  Park  0.20
2  Fast Food Restaurant  

Once again, while these data are interesting, they could be rework to be more human friendly.
Let's define a function to return the Top N venues for a given neighborhood:

In [22]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

With this function, we can now create a new dataframe listing the Top 10 venues per neighborhoods:

In [62]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# Create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# Create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = london_grouped['Neighborhood']

for ind in np.arange(london_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(london_grouped.iloc[ind, :], num_top_venues)

# Check results
print(neighborhoods_venues_sorted.shape)
print('\n')
neighborhoods_venues_sorted.head()

(301, 11)




Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0   Abbey Wood              Pharmacy         Grocery Store   
1        Acton  Gym / Fitness Center                   Pub   
2      Aldgate           Coffee Shop                 Hotel   
3      Aldwych               Theater                 Hotel   
4      Anerley         Grocery Store        Hardware Store   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0        Cosmetics Shop            Playground           IT Services   
1         Train Station              Creperie             Wine Shop   
2          Cocktail Bar            Restaurant  Gym / Fitness Center   
3           Coffee Shop          Burger Joint                   Pub   
4         Train Station                  Park           Zoo Exhibit   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0     Food & Drink Shop        Farmers Market  Fast Food Restaurant   
1                Bakery                  Park                  Café   
2                   Pub      Sushi Restaurant    Italian Restaurant   
3    Italian Restaurant            Restaurant        Cosmetics Shop   
4                  Food  Fast Food Restaurant   Filipino Restaurant   

  9th Most Common Venue     10th Most Common Venue  
0   Filipino Restaurant          Fish & Chips Shop  
1         Grocery Store                  Mini Golf  
2           Pizza Place  Middle Eastern Restaurant  
3                  Park                   Building  
4     Fish & Chips Shop                Fish Market

It is already much better and easier to analyze.
With this dataset, we can proceed to the next step and cluster neighborhoods.

---

## 6. Cluster Neighborhoods

Using the _k_-means method, we will create 5 clusters of the neighborhoods:

In [63]:
# Set number of clusters
kclusters = 10

# Defining the dataframe
london_grouped_clustering = london_grouped.drop('Neighborhood', axis=1)

# Run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(london_grouped_clustering)

# Check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([6, 7, 5, 5, 6, 6, 7, 6, 5, 7])

Now let's merge the clusters with the venues; we will use in inner join to remove potential NaN for which Foursquare didn't retrieve any information:

In [64]:
# Add clustering labels
neighborhoods_venues_clustered = neighborhoods_venues_sorted
neighborhoods_venues_clustered.insert(0, 'Cluster Labels', kmeans.labels_)

london_merged = london_data

# Merge grouped data with original data to add latitude/longitude for each neighborhood
london_merged = london_merged.join(neighborhoods_venues_clustered.set_index('Neighborhood'), on='Neighborhood', how='inner')

# Check results
print(london_merged.shape)
print('\n')
london_merged.head()

(303, 16)




Borough Neighborhood    Town Latitude  Longitude  Cluster Labels  \
0       Bexley   Abbey Wood  London  51.4865   0.109318               6   
1       Ealing        Acton  London  51.5106  -0.264585               7   
2         City      Aldgate  London  51.5149 -0.0783556               5   
3  Westminster      Aldwych  London  51.5128  -0.117388               5   
4      Bromley      Anerley  London  51.4086 -0.0669885               6   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0              Pharmacy         Grocery Store        Cosmetics Shop   
1  Gym / Fitness Center                   Pub         Train Station   
2           Coffee Shop                 Hotel          Cocktail Bar   
3               Theater                 Hotel           Coffee Shop   
4         Grocery Store        Hardware Store         Train Station   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0            Playground           IT Services     Food & Drink Shop   
1              Creperie             Wine Shop                Bakery   
2            Restaurant  Gym / Fitness Center                   Pub   
3          Burger Joint                   Pub    Italian Restaurant   
4                  Park           Zoo Exhibit                  Food   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0        Farmers Market  Fast Food Restaurant   Filipino Restaurant   
1                  Park                  Café         Grocery Store   
2      Sushi Restaurant    Italian Restaurant           Pizza Place   
3            Restaurant        Cosmetics Shop                  Park   
4  Fast Food Restaurant   Filipino Restaurant     Fish & Chips Shop   

      10th Most Common Venue  
0          Fish & Chips Shop  
1                  Mini Golf  
2  Middle Eastern Restaurant  
3                   Building  
4                Fish Market

In [65]:
# Create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# Set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# Add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(london_merged['Latitude'], london_merged['Longitude'], london_merged['Neighborhood'], london_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)

# Display map
map_clusters



---

## 7. Examine Clusters



In [66]:
london_merged.loc[london_merged['Cluster Labels'] == 0,
                  london_merged.columns[[2] + list(range(6, london_merged.shape[1]))]]

Town 1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
55   London              Platform    Chinese Restaurant         Train Station   
70   London              Platform                  Café          Cocktail Bar   
203  London              Platform                  Café                   Pub   
207  London              Platform         Train Station      Asian Restaurant   
217  London              Platform                  Café           Coffee Shop   
230  London              Platform                  Café           Coffee Shop   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
55                   Park     Other Repair Shop     Food & Drink Shop   
70                 Garden         Train Station                 Trail   
203         Train Station        Hardware Store                  Farm   
207           Zoo Exhibit                  Farm  Fast Food Restaurant   
217      Asian Restaurant            Sports Bar              Bus Stop   
230      Asian Restaurant            Sports Bar              Bus Stop   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
55   Fast Food Restaurant   Filipino Restaurant     Fish & Chips Shop   
70   Gym / Fitness Center                  Park      Sculpture Garden   
203  Gym / Fitness Center      Sculpture Garden           Coffee Shop   
207   Filipino Restaurant     Fish & Chips Shop           Fish Market   
217                  Park                   Pub           Gas Station   
230                  Park                   Pub           Gas Station   

    10th Most Common Venue  
55             Fish Market  
70                    Farm  
203     Athletics & Sports  
207            Flea Market  
217          Grocery Store  
230          Grocery Store

In [67]:
london_merged.loc[london_merged['Cluster Labels'] == 1,
                  london_merged.columns[[2] + list(range(6, london_merged.shape[1]))]]

Town 1st Most Common Venue  2nd Most Common Venue  \
17   London             Gastropub                 Bakery   
19   London           Supermarket                   Café   
20   London                  Café                    Pub   
24   London                  Café                 Bakery   
25   London                   Pub                   Café   
38   London              Bus Stop                   Park   
46   London             Gastropub            Coffee Shop   
47   London                  Café      Recreation Center   
76   London                   Pub                   Café   
98   London                  Café          Deli / Bodega   
113  London           Art Gallery                    Bar   
114  London           Art Gallery                    Bar   
115  London                  Café  Vietnamese Restaurant   
118  London                  Café                 Bakery   
120  London                   Pub                   Café   
124  London     Fish & Chips Shop                   Café   
126  London                  Café          Deli / Bodega   
128  London                   Pub                   Café   
136  London                  Café  Vietnamese Restaurant   
151  London                  Café             Restaurant   
154  London                   Pub                   Café   
161  London                  Café                    Pub   
174  London                   Pub                   Café   
179  London                  Café            Coffee Shop   
182  London              Bus Stop                   Café   
194  London                  Café            Coffee Shop   
197  London           Sports Club                   Café   
200  London                   Bar             Restaurant   
206  London                  Café          Grocery Store   
224  London         Go Kart Track                Theater   
228  London                  Café            Coffee Shop   
247  London                   Pub                   Café   
251  London         Train Station                  Trail   
265  London     Convenience Store                    Pub   
267  London                  Café      Indian Restaurant   
268  London                  Café            Sports Club   
273  London                  Café             Restaurant   
278  London                  Café                    Pub   
282  London                   Pub                   Café   
290  London               Brewery                   Park   
299  London                  Café      Indian Restaurant   
302  London                  Café        Nature Preserve   

    3rd Most Common Venue          4th Most Common Venue  \
17                   Café                    Yoga Studio   
19            Zoo Exhibit                     Food Stand   
20     Italian Restaurant                      Hotel Bar   
24                    Pub                  Train Station   
25         Pilates Studio                       Pharmacy   
38                   Café              Electronics Store   
46                   Café             Italian Restaurant   
47      Indian Restaurant              French Restaurant   
76            Coffee Shop          Vietnamese Restaurant   
98                    Pub                    Supermarket   
113                  Café                      Nightclub   
114                  Café                      Nightclub   
115                Bakery                            Pub   
118                   Pub                 Ice Cream Shop   
120                  Park                       Bus Stop   
124     Food & Drink Shop                  Deli / Bodega   
126           Cheese Shop                            Bar   
128    Italian Restaurant                    Supermarket   
136                Bakery                            Pub   
151                 Hotel                            Pub   
154    Italian Restaurant                    Supermarket   
161                   Gym                        Theater   
174                  Farm             Athletic

In [68]:
london_merged.loc[london_merged['Cluster Labels'] == 2,
                  london_merged.columns[[2] + list(range(6, london_merged.shape[1]))]]

Town   1st Most Common Venue   2nd Most Common Venue  \
16   London  Furniture / Home Store                     Pub   
26   London                   Hotel      Italian Restaurant   
53   London                Bus Stop        Sushi Restaurant   
66   London           Grocery Store    Fast Food Restaurant   
71   London                   Beach      Golf Driving Range   
72   London                   Hotel                     Pub   
81   London                   Hotel                     Pub   
90   London       Indian Restaurant  Furniture / Home Store   
125  London             Supermarket                     Gym   
133  London                  Garden          Scenic Lookout   
137  London        Asian Restaurant          Hardware Store   
148  London               Rest Area                Bus Stop   
167  London                   Hotel                     Pub   
169  London                   Hotel       French Restaurant   
170  London                Bus Stop     Fried Chicken Joint   
175  London                   Hotel             Coffee Shop   
181  London          Sandwich Place           Train Station   
186  London             Coffee Shop                Bus Stop   
205  London                   Hotel                     Pub   
213  London              Playground                Bus Stop   
216  London                   Hotel              Restaurant   
229  London                   Hotel                  Bakery   
240  London              Food Truck                   Hotel   
248  London            Soccer Field       Fish & Chips Shop   
266  London                  Garden           Grocery Store   
288  London               Pet Store        Asian Restaurant   
291  London                Bus Stop     Fried Chicken Joint   
292  London                   Hotel             Coffee Shop   

    3rd Most Common Venue 4th Most Common Venue  5th Most Common Venue  \
16   Gym / Fitness Center        Clothing Store          Grocery Store   
26              Hotel Bar  Gym / Fitness Center         Sandwich Place   
53                   Park                 Hotel            Zoo Exhibit   
66            Coffee Shop                 Hotel               Bus Stop   
71               Bus Stop             Pet Store             Nail Salon   
72              Hotel Bar                Bridge       Tapas Restaurant   
81                   Café           Pizza Place    Lebanese Restaurant   
90      Fish & Chips Shop           Zoo Exhibit             Food Court   
125        Cosmetics Shop          Soccer Field                  Hotel   
133           Golf Course            Playground            Zoo Exhibit   
137              Bus Stop                  Café            Supermarket   
148          Soccer Field         Bowling Alley             Food Court   
167              Bus Stop     Indian Restaurant                   Café   
169            Restaurant             Hotel Bar                 Lounge   
170   Japanese Restaurant                  Café                   Park   
175        Sandwich Place      Sushi Restaurant              Hotel Bar   
181         Metro Station              Bus Stop  Portuguese Restaurant   
186            Restaurant           Supermarket                  Trail   
205                  Park                  Café     Turkish Restaurant   
213  Gym / Fitness Center                  Pool            Zoo Exhibit   
216                  Café                   Pub        Harbor / Marina   
229          Burger Joint    Italian Restaurant                    Pub   
240                  Park    Italian Restaurant   Gym / Fitness Center   
248         Grocery Store                 Hotel                  Plaza   
266            Playground                 Hotel            Zoo Exhibit   
288   Sporting Goods Shop           Supermarket         Hardware Store   
291   Japanese Restaurant                  Café                   Park   
292        Sandwich Place      Sushi Restaurant              Hotel Bar   

          6th Most Common Venue 

In [69]:
london_merged.loc[london_merged['Cluster Labels'] == 3,
                  london_merged.columns[[2] + list(range(6, london_merged.shape[1]))]]

Town 1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
82  London    Italian Restaurant           Zoo Exhibit            Food Stand   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
82        Farmers Market  Fast Food Restaurant   Filipino Restaurant   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
82     Fish & Chips Shop           Fish Market           Flea Market   

   10th Most Common Venue  
82            Flower Shop

In [70]:
london_merged.loc[london_merged['Cluster Labels'] == 4,
                  london_merged.columns[[2] + list(range(6, london_merged.shape[1]))]]

Town 1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
12   London                   Pub                Forest           Zoo Exhibit   
79   London                Forest           Zoo Exhibit            Food Court   
222  London                Castle                   Pub                  Café   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
12             Food Court        Farmers Market  Fast Food Restaurant   
79         Farmers Market  Fast Food Restaurant   Filipino Restaurant   
222                Forest           Zoo Exhibit            Food Court   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
12    Filipino Restaurant     Fish & Chips Shop           Fish Market   
79      Fish & Chips Shop           Fish Market           Flea Market   
222  Fast Food Restaurant   Filipino Restaurant     Fish & Chips Shop   

    10th Most Common Venue  
12             Flea Market  
79             Flower Shop  
222            Fish Market

In [71]:
london_merged.loc[london_merged['Cluster Labels'] == 5,
                  london_merged.columns[[2] + list(range(6, london_merged.shape[1]))]]

Town    1st Most Common Venue      2nd Most Common Venue  \
2    London              Coffee Shop                      Hotel   
3    London                  Theater                      Hotel   
8    London                      Pub                Coffee Shop   
10   London              Coffee Shop                 Food Truck   
11   London                     Park          Food & Drink Shop   
13   London              Coffee Shop                       Café   
14   London   Furniture / Home Store          Convenience Store   
15   London                      Pub                Coffee Shop   
18   London       Italian Restaurant                       Café   
21   London                      Pub                Coffee Shop   
22   London                     Café                Coffee Shop   
23   London                      Pub       Gym / Fitness Center   
27   London                      Pub                      Hotel   
29   London              Coffee Shop                        Pub   
30   London                 Bus Stop          Food & Drink Shop   
31   London              Coffee Shop             Clothing Store   
32   London  Scandinavian Restaurant             Sandwich Place   
33   London     Caribbean Restaurant                Pizza Place   
34   London              Coffee Shop         Chinese Restaurant   
36   London       Italian Restaurant                       Café   
37   London                      Pub                   Bus Stop   
39   London              Coffee Shop       Gym / Fitness Center   
40   London                     Café                   Bus Stop   
41   London              Coffee Shop                        Pub   
43   London              Coffee Shop               Burger Joint   
44   London                      Pub              Grocery Store   
49   London                     Café                        Pub   
50   London                  Theater                      Hotel   
51   London            Train Station         Chinese Restaurant   
57   London                      Pub                       Park   
58   London                      Pub                     Bakery   
59   London                      Pub                     Bakery   
60   London                      Pub                       Café   
61   London                      Pub                Coffee Shop   
62   London     Fast Food Restaurant       Gym / Fitness Center   
65   London              Coffee Shop             Ice Cream Shop   
67   London              Coffee Shop         Chinese Restaurant   
69   London                      Pub                       Pool   
73   London                      Pub                     Bakery   
74   London                      Pub         Italian Restaurant   
75   London                     Café                        Pub   
77   London              Coffee Shop                   Platform   
80   London              Coffee Shop             Clothing Store   
85   London                 Gym Pool                  Bookstore   
86   London              Coffee Shop              Grocery Store   
88   London                      Pub                   Bus Stop   
89   London     Fast Food Restaurant                        Pub   
91   London              Coffee Shop                        Pub   
92   London       Turkish Restaurant                Supermarket   
93   London                      Pub                Coffee Shop   
94   London                      Pub                Coffee Shop   
95   London              Coffee Shop             Clothing Store   
100  London                     Café                     Bakery   
101  London       Italian Restaurant                       Café   
102  London       Italian Restaurant                Coffee Shop   
103  London              Coffee Shop              Grocery Store   
104  London     Gym / Fitness Center         Italian Restaurant   
106  London              Golf Course                Zoo Exhibit   
110  London              Coffee Shop             Sandw

In [72]:
london_merged.loc[london_merged['Cluster Labels'] == 6,
                  london_merged.columns[[2] + list(range(6, london_merged.shape[1]))]]

Town     1st Most Common Venue     2nd Most Common Venue  \
0    London                  Pharmacy             Grocery Store   
4    London             Grocery Store            Hardware Store   
5    London                      Park             Grocery Store   
7    London        Chinese Restaurant                  Beer Bar   
48   London       Fried Chicken Joint      Other Great Outdoors   
63   London             Grocery Store                  Platform   
64   London             Grocery Store        Italian Restaurant   
78   London        Chinese Restaurant             Historic Site   
84   London             Grocery Store        Italian Restaurant   
96   London             Grocery Store             Train Station   
99   London             Grocery Store        Italian Restaurant   
108  London                  Platform             Grocery Store   
109  London                  Platform             Grocery Store   
116  London  Mediterranean Restaurant            Shop & Service   
156  London             Grocery Store  Mediterranean Restaurant   
160  London       Fried Chicken Joint             Grocery Store   
183  London        Chinese Restaurant      Fast Food Restaurant   
184  London        Chinese Restaurant                  Beer Bar   
187  London  Mediterranean Restaurant      Gym / Fitness Center   
195  London             Train Station               Bus Station   
196  London             Grocery Store                    Garden   
233  London                      Park             Grocery Store   
234  London             Train Station                      Park   
245  London                      Park             Grocery Store   
274  London             Grocery Store  Mediterranean Restaurant   
280  London             Grocery Store                    Garden   
287  London               Supermarket             Grocery Store   

    3rd Most Common Venue 4th Most Common Venue       5th Most Common Venue  \
0          Cosmetics Shop            Playground                 IT Services   
4           Train Station                  Park                 Zoo Exhibit   
5    Fast Food Restaurant                Bakery                Tram Station   
7                    Park         Grocery Store                 Zoo Exhibit   
48            Coffee Shop         Grocery Store                 Zoo Exhibit   
63            Supermarket         Train Station           Fish & Chips Shop   
64           Dessert Shop            Playground                 Coffee Shop   
78                Brewery         Grocery Store                 Zoo Exhibit   
84               Bus Stop                Bakery                         Pub   
96   Fast Food Restaurant    Chinese Restaurant                      Bakery   
99      Fish & Chips Shop          Dessert Shop                 Zoo Exhibit   
108                   Pub         Train Station        Gym / Fitness Center   
109                   Pub         Train Station        Gym / Fitness Center   
116  Fast Food Restaurant         Grocery Store           Food & Drink Shop   
156              Bus Stop            Sports Bar        Gym / Fitness Center   
160     Indian Restaurant        Ice Cream Shop            Asian Restaurant   
183              Bus Stop          Soccer Field               Grocery Store   
184                  Park         Grocery Store                 Zoo Exhibit   
187         Grocery Store     Convenience Store  Construction & Landscaping   
195                   Gym         Grocery Store  Modern European Restaurant   
196                   Pub                 Plaza                  Food Court   
233        Hardware Store          Concert Hall   South American Restaurant   
234                   Gym         Grocery Store                 Zoo Exhibit   
245                 Hotel                  Farm         Fried Chicken Joint   
274              Bus Stop            Sports Bar        Gym / Fitness Center   
280            Restaurant              Bus Stop                         Gym 

In [73]:
london_merged.loc[london_merged['Cluster Labels'] == 7,
                  london_merged.columns[[2] + list(range(6, london_merged.shape[1]))]]

Town 1st Most Common Venue   2nd Most Common Venue  \
1    London  Gym / Fitness Center                     Pub   
6    London                   Pub       Indian Restaurant   
9    London                   Pub                    Café   
28   London                   Pub             Coffee Shop   
35   London              Bus Stop                     Pub   
42   London                   Pub                    Park   
45   London          Tennis Court                    Park   
52   London                   Pub                  Garden   
56   London                   Pub                    Café   
68   London       Nature Preserve                    Park   
83   London                   Pub                    Café   
87   London             Bookstore      Turkish Restaurant   
97   London         Garden Center         Nature Preserve   
105  London                  Park          History Museum   
107  London           Zoo Exhibit                    Tree   
119  London                  Park   Outdoors & Recreation   
127  London                   Pub       Indian Restaurant   
134  London          Soccer Field                    Park   
141  London                   Pub           Train Station   
144  London          Soccer Field                    Park   
150  London                   Pub                    Park   
152  London                  Park            Skating Rink   
171  London          Tram Station                    Park   
178  London     Convenience Store       Other Repair Shop   
185  London                   Pub                    Café   
192  London                   Pub                  Garden   
193  London                   Pub             Coffee Shop   
199  London                  Farm      Turkish Restaurant   
210  London                   Pub             Coffee Shop   
212  London    Chinese Restaurant                     Pub   
220  London    Chinese Restaurant                     Pub   
235  London                   Pub  Furniture / Home Store   
257  London           Sports Club            Soccer Field   
260  London                   Pub           Train Station   
272  London              Bus Line                Bus Stop   
285  London              Bus Line                Bus Stop   
293  London                   Pub             Coffee Shop   
304  London       Nature Preserve           Track Stadium   

    3rd Most Common Venue       4th Most Common Venue 5th Most Common Venue  \
1           Train Station                    Creperie             Wine Shop   
6             Coffee Shop                   Jazz Club              Tea Room   
9                    Park          Italian Restaurant                Garden   
28         Breakfast Spot                        Café     Convenience Store   
35           Burger Joint                      Office                  Café   
42          Garden Center                        Café           Event Space   
45      Convenience Store  Construction & Landscaping            Food Stand   
52          Grocery Store           French Restaurant           Pizza Place   
56     Italian Restaurant                       Hotel                  Park   
68            Social Club                 Zoo Exhibit     Food & Drink Shop   
83      Fish & Chips Shop                        Park         Grocery Store   
87                    Pub                        Park           Supermarket   
97                    Pub              Scenic Lookout     Food & Drink Shop   
105             Gift Shop        Gym / Fitness Center                   Pub   
107                Garden                         Pub         Historic Site   
119             Bookstore                  Food Stand   Filipino Restaurant   
127           Coffee Shop                   Jazz Club              Tea Room   
134            Laundromat                 Zoo Exhibit     Food & Drink Shop   
141                Hostel        Gym / Fitness Center           Supermarket   
144           Zoo Exhibit                      

In [74]:
london_merged.loc[london_merged['Cluster Labels'] == 8,
                  london_merged.columns[[2] + list(range(6, london_merged.shape[1]))]]

Town 1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
214  London              Bus Stop  Gym / Fitness Center           Zoo Exhibit   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
214            Food Stand   Filipino Restaurant     Fish & Chips Shop   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
214           Fish Market           Flea Market           Flower Shop   

    10th Most Common Venue  
214                   Food

In [75]:
london_merged.loc[london_merged['Cluster Labels'] == 9,
                  london_merged.columns[[2] + list(range(6, london_merged.shape[1]))]]

Town 1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
54   London          Home Service                Lounge           Zoo Exhibit   
225  London          Home Service                Lounge           Zoo Exhibit   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
54      Food & Drink Shop        Farmers Market  Fast Food Restaurant   
225     Food & Drink Shop        Farmers Market  Fast Food Restaurant   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
54    Filipino Restaurant     Fish & Chips Shop           Fish Market   
225   Filipino Restaurant     Fish & Chips Shop           Fish Market   

    10th Most Common Venue  
54             Flea Market  
225            Flea Market